In [1]:
import warnings

warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')

In [4]:
import pandas as pd
from IPython.display import HTML, display
from transformers import GPT2Tokenizer
import re

tokenizer = GPT2Tokenizer.from_pretrained("gpt2")

In [5]:
df = pd.read_csv('story_datasets.csv')

engines = [ "davinci-002", "curie-001", "babbage-001", "ada-001" ]

def clean(text):
    tokens = tokenizer(text)['input_ids']
    return tokenizer.decode(tokens)
    
def shorten(row):
    max_len = max(len(row[e]) for e in engines)
    cutoff = 0
    
    for m in re.finditer(r"[\.?!](\")?", row['ref']):
        if len(row['ref'][:m.end()]) >= max_len:
            break
        else:
            cutoff = m.end()
    
    return row['ref'][:cutoff]

df['ref'] = df.apply(shorten, axis=1)

# Which author is the better fiction writer?

5 writers (a mix of humans and AI writing systems) -- named **A, B, C, D, E** -- were given 5 writing prompts. For each prompt, they were asked to write a fictional story of a few sentences. Carefully read each prompt and each writer's brief continuation of that prompt.

To begin, please enter your ReaderID below and click 'SEE TEXT' (scroll down to read all of the prompts). After reading, **please go back to Mechanical Turk and fill out the survey**.

In [9]:
output = []

for i in range(0, df['agent'].max() + 1):
    df_i = df[df['agent'] == i].drop(['agent'], axis=1)
    df_i = df_i[df['prompt'].apply(lambda p: '?' not in p)]
    
    df_i = df_i.sample(n=5, random_state=i)
    df_i.index = list(range(1, len(df_i) + 1))
    
    if len(df_i) < 5:
        print(i)

    df_i = df_i.rename(columns={
        "ref" : "E",
        "davinci-002": "D",
        "curie-001" : "C",
        "babbage-001" : "B",
        "ada-001" : "A",
    })[['prompt','A', 'B', 'C', 'D', 'E']]

    s = df_i.style
    s.set_properties(**{
        'text-align': 'left',
        'white-space': 'pre-wrap',
        'vertical-align': 'top',
        'width':'50em',
    }, overwrite=False)
    s.set_table_styles([
        {'selector': 'tbody th', 'props': 'position: sticky; left:0; background-color:white;'},
        {'selector': 'thead th', 'props': 'position: sticky; top:0; background-color:black; color: white; text-align:center'},
    ], overwrite=False)

    output.append(f"<div class='agent' id='agent{i}' style='display:none'>" + s.to_html() + "</div>")
    
# display(HTML(
# """
# <style>
# table {table-layout: fixed;}
# </style>
# """
# ))

display(HTML(
"""
<p class="jp-Cell">
Enter your ReaderID: <input id="myInput" type="number" value="0" min="%s" max="%s">
<button id="myBtn" onclick="makeVisible()">SEE TEXT</button>
</p>
""" % (df['agent'].min(), df['agent'].max())
))

display(HTML("<center><div style='max-height: 52vh; width: 100%; overflow-y: scroll;'>" + ''.join(output) + "</div></center>"))

display(HTML(
"""
<script>
var input = document.getElementById("myInput");
input.addEventListener("keypress", function(event) {
  if (event.key === "Enter") {
    event.preventDefault();
    document.getElementById("myBtn").click();
  }
});

function makeVisible() {
  var val = document.getElementById("myInput").value;  
  var elems = document.getElementsByClassName('agent');
  for (var i=0;i<elems.length;i+=1){
    elems[i].style.display = 'none';
  }

  document.getElementById("agent" + val).style.display = 'block';
}
</script>
""" 
))
